In [1]:
#import all the necessary packages

import pandas as pd
import random

import nltk
nltk.download('punkt')
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
from nltk import stem
stemmer = stem.PorterStemmer()
from nltk import word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
stops = set(stopwords.words('english'))
import string
punct = list(string.punctuation)
from collections import Counter
import requests
import seaborn as sns
sns.set()
import matplotlib.pyplot as plt
import numpy as np
import praw
import datetime
import json
import re

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\aoife\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\aoife\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [2]:
import PyPDF2

In [4]:
# open the PDF file
equalityact = open(r'C:\Users\aoife\Documents\Capstone\1 Coding\AA Equality Act 2010.pdf', 'rb')

# create a PDF reader object
pdf_reader = PyPDF2.PdfReader(equalityact)

# read the text from each page
text = ''
for page_num in range(len(pdf_reader.pages)):
    page = pdf_reader.pages[page_num]
    text += page.extract_text()

# close the PDF file
equalityact.close()

In [5]:
# split the text into sentences
sentences = re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', text)

# create a dataframe with the sentences as rows
df = pd.DataFrame({'Sentence': sentences})

In [6]:
df

Sentence
0      Status: This version of this Act contains prov...
1      Changes to legislation: Equality Act 2010 is u...
2      There are changes that may be brought into for...
3      Changes that have been made appear\nin the con...
4      (See end of Document for details) View outstan...
...                                                  ...
11008                                             51  s.
11009                                         2(b)\n– s.
11010                           124A inserted by 2023 c.
11011                                             51  s.
11012                                                  3

[11013 rows x 1 columns]

In [7]:
#check to see if any rows are empty
rows_with_nan = df[df.isna().any(axis=1)]

len(rows_with_nan)

0

In [8]:
#check the length of the dataframe
len(df)

11013

In [9]:
# convert each row in the dataframe to a string and then convert the datadrame to a list of strings
eq_act = df.apply(lambda row: ' '.join(row.astype(str)), axis=1).tolist()

In [10]:
eq_act

['Status: This version of this Act contains provisions that are prospective.',
 'Changes to legislation: Equality Act 2010 is up to date with all changes known to be in force on or before 08 May\n2024.',
 'There are changes that may be brought into force at a future date.',
 'Changes that have been made appear\nin the content and are referenced with annotations.',
 '(See end of Document for details) View outstanding changes\nEquality Act 2010\n2010 CHAPTER 15\nAn Act to make provision to require Ministers of the Crown and others when making\nstrategic decisions about the exercise of their functions to have regard to the desirability\nof reducing socio-economic inequalities; to reform and harmonise equality law and\nrestate the greater part of the enactments relating to discrimination and harassment\nrelated to certain personal characteristics; to enable certain employers to be required to\npublish information about the differences in pay between male and female employees;\nto prohibit 

In [11]:
# define a function to remove punctuation and numbers from a string
def remove_punctuation_and_numbers(text):
    # define a regular expression pattern to match punctuation characters and numbers
    pattern = r'[^A-Za-z\s]'
    # replace punctuation characters and numbers with an empty string
    cleaned_text = re.sub(pattern, '', text)
    return cleaned_text

# apply the previously created function to each string in the list
cleaned_eq_act = [remove_punctuation_and_numbers(string) for string in eq_act]

# display the cleaned list of strings
print(cleaned_eq_act)

['Status This version of this Act contains provisions that are prospective', 'Changes to legislation Equality Act  is up to date with all changes known to be in force on or before  May\n', 'There are changes that may be brought into force at a future date', 'Changes that have been made appear\nin the content and are referenced with annotations', 'See end of Document for details View outstanding changes\nEquality Act \n CHAPTER \nAn Act to make provision to require Ministers of the Crown and others when making\nstrategic decisions about the exercise of their functions to have regard to the desirability\nof reducing socioeconomic inequalities to reform and harmonise equality law and\nrestate the greater part of the enactments relating to discrimination and harassment\nrelated to certain personal characteristics to enable certain employers to be required to\npublish information about the differences in pay between male and female employees\nto prohibit victimisation in certain circumstanc

In [12]:
# tokenize each string in the list of strings
tokenized_eq_act = [word_tokenize(string) for string in cleaned_eq_act]

# display the tokenized list of strings
print(tokenized_eq_act)

[['Status', 'This', 'version', 'of', 'this', 'Act', 'contains', 'provisions', 'that', 'are', 'prospective'], ['Changes', 'to', 'legislation', 'Equality', 'Act', 'is', 'up', 'to', 'date', 'with', 'all', 'changes', 'known', 'to', 'be', 'in', 'force', 'on', 'or', 'before', 'May'], ['There', 'are', 'changes', 'that', 'may', 'be', 'brought', 'into', 'force', 'at', 'a', 'future', 'date'], ['Changes', 'that', 'have', 'been', 'made', 'appear', 'in', 'the', 'content', 'and', 'are', 'referenced', 'with', 'annotations'], ['See', 'end', 'of', 'Document', 'for', 'details', 'View', 'outstanding', 'changes', 'Equality', 'Act', 'CHAPTER', 'An', 'Act', 'to', 'make', 'provision', 'to', 'require', 'Ministers', 'of', 'the', 'Crown', 'and', 'others', 'when', 'making', 'strategic', 'decisions', 'about', 'the', 'exercise', 'of', 'their', 'functions', 'to', 'have', 'regard', 'to', 'the', 'desirability', 'of', 'reducing', 'socioeconomic', 'inequalities', 'to', 'reform', 'and', 'harmonise', 'equality', 'law', '

In [13]:
# as some strings are now empty, remove empty strings from a list of strings
cleaned_list_of_strings = [string for string in tokenized_eq_act if string]

# and just in case that doesn't work,, remove empty strings from a list of lists of strings
cleaned_tokenized_eq_act = [[token for token in tokens if token] for tokens in tokenized_eq_act]

In [14]:
cleaned_tokenized_eq_act

[['Status',
  'This',
  'version',
  'of',
  'this',
  'Act',
  'contains',
  'provisions',
  'that',
  'are',
  'prospective'],
 ['Changes',
  'to',
  'legislation',
  'Equality',
  'Act',
  'is',
  'up',
  'to',
  'date',
  'with',
  'all',
  'changes',
  'known',
  'to',
  'be',
  'in',
  'force',
  'on',
  'or',
  'before',
  'May'],
 ['There',
  'are',
  'changes',
  'that',
  'may',
  'be',
  'brought',
  'into',
  'force',
  'at',
  'a',
  'future',
  'date'],
 ['Changes',
  'that',
  'have',
  'been',
  'made',
  'appear',
  'in',
  'the',
  'content',
  'and',
  'are',
  'referenced',
  'with',
  'annotations'],
 ['See',
  'end',
  'of',
  'Document',
  'for',
  'details',
  'View',
  'outstanding',
  'changes',
  'Equality',
  'Act',
  'CHAPTER',
  'An',
  'Act',
  'to',
  'make',
  'provision',
  'to',
  'require',
  'Ministers',
  'of',
  'the',
  'Crown',
  'and',
  'others',
  'when',
  'making',
  'strategic',
  'decisions',
  'about',
  'the',
  'exercise',
  'of',
  't

In [15]:
#lemmatize
postlemma = []

for i in cleaned_tokenized_eq_act: 
    postlemma.append([lemmatizer.lemmatize(j) for j in i])

In [16]:
postlemma

[['Status',
  'This',
  'version',
  'of',
  'this',
  'Act',
  'contains',
  'provision',
  'that',
  'are',
  'prospective'],
 ['Changes',
  'to',
  'legislation',
  'Equality',
  'Act',
  'is',
  'up',
  'to',
  'date',
  'with',
  'all',
  'change',
  'known',
  'to',
  'be',
  'in',
  'force',
  'on',
  'or',
  'before',
  'May'],
 ['There',
  'are',
  'change',
  'that',
  'may',
  'be',
  'brought',
  'into',
  'force',
  'at',
  'a',
  'future',
  'date'],
 ['Changes',
  'that',
  'have',
  'been',
  'made',
  'appear',
  'in',
  'the',
  'content',
  'and',
  'are',
  'referenced',
  'with',
  'annotation'],
 ['See',
  'end',
  'of',
  'Document',
  'for',
  'detail',
  'View',
  'outstanding',
  'change',
  'Equality',
  'Act',
  'CHAPTER',
  'An',
  'Act',
  'to',
  'make',
  'provision',
  'to',
  'require',
  'Ministers',
  'of',
  'the',
  'Crown',
  'and',
  'others',
  'when',
  'making',
  'strategic',
  'decision',
  'about',
  'the',
  'exercise',
  'of',
  'their',


In [17]:
#lower all cases
postfin1 = [[j.lower() for j in i] for i in postlemma]

In [18]:
postfin1

[['status',
  'this',
  'version',
  'of',
  'this',
  'act',
  'contains',
  'provision',
  'that',
  'are',
  'prospective'],
 ['changes',
  'to',
  'legislation',
  'equality',
  'act',
  'is',
  'up',
  'to',
  'date',
  'with',
  'all',
  'change',
  'known',
  'to',
  'be',
  'in',
  'force',
  'on',
  'or',
  'before',
  'may'],
 ['there',
  'are',
  'change',
  'that',
  'may',
  'be',
  'brought',
  'into',
  'force',
  'at',
  'a',
  'future',
  'date'],
 ['changes',
  'that',
  'have',
  'been',
  'made',
  'appear',
  'in',
  'the',
  'content',
  'and',
  'are',
  'referenced',
  'with',
  'annotation'],
 ['see',
  'end',
  'of',
  'document',
  'for',
  'detail',
  'view',
  'outstanding',
  'change',
  'equality',
  'act',
  'chapter',
  'an',
  'act',
  'to',
  'make',
  'provision',
  'to',
  'require',
  'ministers',
  'of',
  'the',
  'crown',
  'and',
  'others',
  'when',
  'making',
  'strategic',
  'decision',
  'about',
  'the',
  'exercise',
  'of',
  'their',


In [19]:
# replace the old comments with the new pre-processed comments
data = {'Sentence': postfin1}
eq_act = pd.DataFrame(data)

In [20]:
eq_act

Sentence
0      [status, this, version, of, this, act, contain...
1      [changes, to, legislation, equality, act, is, ...
2      [there, are, change, that, may, be, brought, i...
3      [changes, that, have, been, made, appear, in, ...
4      [see, end, of, document, for, detail, view, ou...
...                                                  ...
11008                                                [s]
11009                                             [b, s]
11010                               [a, inserted, by, c]
11011                                                [s]
11012                                                 []

[11013 rows x 1 columns]

In [21]:
# set display options to show all columns and rows in the dataframe so i can quickly scan through
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', None)

# display the dataframe
print(eq_act)

                                                Sentence
0      [status, this, version, of, this, act, contain...
1      [changes, to, legislation, equality, act, is, ...
2      [there, are, change, that, may, be, brought, i...
3      [changes, that, have, been, made, appear, in, ...
4      [see, end, of, document, for, detail, view, ou...
5      [th, april, be, it, enacted, by, the, queens, ...
6      [not, altering, text, c, act, applied, by, the...
7                      [b, c, act, applied, by, si, art]
8      [c, a, amended, by, the, channel, tunnel, inte...
9                         [c, act, applied, by, si, art]
10     [a, a, amended, by, the, channel, tunnel, inte...
11                       [c, act, modified, by, si, art]
12     [a, amended, by, the, nationality, immigration...
13                                 [b, equality, act, c]
14     [part, socioeconomic, inequality, document, ge...
15     [changes, to, legislation, equality, act, is, ...
16     [there, are, change, tha

In [22]:
# Doing so helped me notice that there are a bunch of empty lists, so we will remove those now
# find rows with empty lists in the 'Sentence' column
rows_with_empty_lists = eq_act[eq_act['Sentence'].apply(len) == 0]

# display rows with empty lists
print(rows_with_empty_lists)

      Sentence
30          []
31          []
32          []
33          []
34          []
35          []
36          []
37          []
38          []
39          []
40          []
41          []
42          []
43          []
44          []
45          []
46          []
47          []
48          []
49          []
50          []
51          []
52          []
53          []
54          []
55          []
56          []
57          []
58          []
59          []
60          []
62          []
63          []
64          []
65          []
66          []
67          []
68          []
69          []
70          []
71          []
72          []
73          []
74          []
75          []
76          []
77          []
78          []
79          []
80          []
81          []
82          []
83          []
84          []
85          []
86          []
87          []
88          []
89          []
90          []
91          []
92          []
165         []
166         []
167         []
168       

In [23]:
# remove rows with empty lists in the 'Sentence' column
eq_act = eq_act[eq_act['Sentence'].apply(len) > 0]

# reset index
eq_act.reset_index(drop=True, inplace=True)

# display the modified DataFrame
print(eq_act)

                                               Sentence
0     [status, this, version, of, this, act, contain...
1     [changes, to, legislation, equality, act, is, ...
2     [there, are, change, that, may, be, brought, i...
3     [changes, that, have, been, made, appear, in, ...
4     [see, end, of, document, for, detail, view, ou...
5     [th, april, be, it, enacted, by, the, queens, ...
6     [not, altering, text, c, act, applied, by, the...
7                     [b, c, act, applied, by, si, art]
8     [c, a, amended, by, the, channel, tunnel, inte...
9                        [c, act, applied, by, si, art]
10    [a, a, amended, by, the, channel, tunnel, inte...
11                      [c, act, modified, by, si, art]
12    [a, amended, by, the, nationality, immigration...
13                                [b, equality, act, c]
14    [part, socioeconomic, inequality, document, ge...
15    [changes, to, legislation, equality, act, is, ...
16    [there, are, change, that, may, be, brough

In [24]:
# just to check it is still all good in this format too (can't be too careful)
eq_act

Sentence
0     [status, this, version, of, this, act, contain...
1     [changes, to, legislation, equality, act, is, ...
2     [there, are, change, that, may, be, brought, i...
3     [changes, that, have, been, made, appear, in, ...
4     [see, end, of, document, for, detail, view, ou...
5     [th, april, be, it, enacted, by, the, queens, ...
6     [not, altering, text, c, act, applied, by, the...
7                     [b, c, act, applied, by, si, art]
8     [c, a, amended, by, the, channel, tunnel, inte...
9                        [c, act, applied, by, si, art]
10    [a, a, amended, by, the, channel, tunnel, inte...
11                      [c, act, modified, by, si, art]
12    [a, amended, by, the, nationality, immigration...
13                                [b, equality, act, c]
14    [part, socioeconomic, inequality, document, ge...
15    [changes, to, legislation, equality, act, is, ...
16    [there, are, change, that, may, be, brought, i...
17    [changes, that, have, been, made, appear, in, ...
18    [see, end, of, document, for, detail, view, ou...
19    [in, deciding, how, to, fulfil, a, duty, to, w...
20    [fa, the, guidance, to, be, taken, into, accou...
21    [fthe, authority, to, which, this, section, ap...
22    [scotland, act, h, an, integration, joint, boa...
23    [fn, scottish, national, investment, bank, plc...
24    [fa, this, section, also, applies, to, the, fo...
25    [part, socioeconomic, inequality, document, ge...
26    [changes, to, legislation, equality, act, is, ...
27    [there, are, change, that, may, be, brought, i...
28    [changes, that, have, been, made, appear, in, ...
29    [see, end, of, document, for, detail, view, ou...
30                                                  [f]
31    [the, reference, to, inequality, in, subsectio...
32               [textual, amendments, f, words, in, s]
33                  [substituted, by, scotland, act, c]
34                                                  [s]
35                                               [f, s]
36                  [a, inserted, by, scotland, act, c]
37                                                  [s]
38                                               [f, s]
39                   [aaa, inserted, by, wales, act, c]
40                                                  [s]
41                                          [with, sch]
42                                               [para]
43                                            [si, reg]
44                                            [i, f, s]
45    [substituted, s, by, the, equality, act, autho...
46                                               [f, s]
47    [aba, inserted, by, the, equality, act, author...
48                                               [f, s]
49    [h, omitted, ew, by, virtue, of, health, and, ...
50                                                  [s]
51                                                [sch]
52                                               [para]
53                                         [a, si, art]
54                                          [with, art]
55                                               [f, s]
56    [i, omitted, by, virtue, of, health, and, soci...
57                                                  [s]
58                                                [sch]
59                                               [para]
60                                         [b, si, art]
61                                          [with, art]
62                                               [f, s]
63    [j, repealed, at, am, by, public, bodies, act, c]
64                                                  [s]
65                                                [sch]
66                                            [si, art]
67                                 [b, f, words, in, s]
68    [k, substituted, by, police, reform, and, soci...
69                                                  [s]
70                                                [sch]
71             

In [25]:
# save the dataset to be able to use in analysis

#export to excel file
eq_act.to_excel('eq_act.xlsx')

#export to csv file
eq_act.to_csv('eq_act.csv', index=False)